In [7]:
# Packages and initialisations
import os,sys # to access the system
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
%config InlineBackend.figure_format = 'retina'

camb_installation_path = './CAMB'
camb_path = os.path.realpath(os.path.join(os.getcwd(),camb_installation_path))
sys.path.insert(0,camb_path)

import camb
from camb import *

ModuleNotFoundError: No module named 'camb'

# Cosmic Microwave Background (CMB) 

In [2]:
from IPython.display import Video

Video("images/CMB.mp4",embed=True,width=1024, height=576)

## Cool CMB MAP simulator:

(https://chrisnorth.github.io/planckapps/Simulator/)

In [3]:
TT=pd.read_csv("../data/Planck_TT.txt", sep='\s+')
TT=pd.read_csv("../data/Planck_TT.txt", sep='\s+',header=None, skiprows=1, names=TT.keys()[1:len(TT.keys())])

In [4]:
LCDM_params=camb.read_ini(os.path.join(camb_path,'inifiles','planck_2018.ini'))

my_params = model.CAMBparams()
    
my_params = camb.set_params(
    #----Standard 6 params-----
    H0=73,
    ombh2=0.022,
    omch2=0.12,
    tau=0.054,
    ns=0.96,
    As=2.1e-9,
    #---- Other key Params-----
    w=-1, # Dark Energy EOS -> w=-1 means P=-ρ
    wa=0, # Dynamical Dark Energy: wDE = w + wa(1 − a) 
    nrun=0, # running of the sectral index dns/dlogk
    nrunrun=0, # running of running of the sectral index dnrun/dlogk
    omk=0, # curvature density parameter (<0 closed, =0 flat, >0 open)
    mnu=0.06, # total neutrino mass (sum over neutrino species)
    nnu=3.044, # effective number of relativistic particles in the early Universe (SM is nnu=3.44)
    Alens=1 # lensing Amplitude (=1 GR, >1 more lensing than GR)
)

NameError: name 'camb' is not defined

In [ ]:
LCDM_results = camb.get_results(LCDM_params)
LCDM_powers = LCDM_results.get_cmb_power_spectra(LCDM_params, CMB_unit='muK')

my_results=camb.get_results(my_params)
my_powers=my_results.get_cmb_power_spectra(my_params, CMB_unit='muK')

In [ ]:
fig, ax = plt.subplots(1,1, figsize = (7,4))

LCDM_TT=LCDM_powers['total'][2:,0]
LCDM_ell=np.arange(LCDM_TT.shape[0])
my_TT=my_powers['total'][2:,0]
my_ell=np.arange(my_TT.shape[0])

ax.set_xscale("log")

ax.set_ylabel(r'$D_{\ell}^{TT}$ [$\mu K^2$]')

ax.plot(LCDM_ell,LCDM_TT, color='Darkred', label=r"$\Lambda$CDM")
ax.plot(my_ell,my_TT, color='Darkgreen', label=r"My model")

ax.scatter(TT["l"],TT["Dl"],c="k",s=10, marker='o', edgecolors= "k")
ax.errorbar(TT["l"],TT["Dl"],yerr=[TT["-dDl"],TT["+dDl"]], alpha=1,color="k", marker='None',capsize=1, capthick=1,linestyle="none")

ax.axvline(30,color='grey', ls="--")
ax.legend(loc='upper left')

# Baryon Acoustic Oscillation (BAO)

In [ ]:
from IPython.display import Video

Video("images/BAO.mp4",embed=True,width=1024, height=576)

In [ ]:
# BAO DATA

BAO=pd.read_csv("../data/BAO_SDSS.txt", sep='\s+')
BAO=pd.read_csv("../data/BAO_SDSS.txt", sep='\s+',header=None, skiprows=1, names=BAO.keys()[1:len(BAO.keys())])

DV_rs=BAO[BAO['type'].isin(['D_V/rs'])] 
DM_rs=BAO[BAO['type'].isin(['D_M/rs'])] 
c_Hrs=BAO[BAO['type'].isin(['c/Hrs'])] 

In [ ]:
def get_distances(model):
    
    results=camb.get_results(model)
    
    c=299792.458 #km/s

    z = np.linspace(0.01,4,100)

    DA = results.angular_diameter_distance(z)

    H=results.get_BAO(z,model)[:,1]

    rdrag=results.get_derived_params()['rdrag']
    print('Sound Horizon=', rdrag)

    DM=(1+z)*DA
    DH= c/H
    DV= ((c*z*DM**2)/H)**(1/3)

    y1 = DV/(rdrag*z**0.5)
    y2 = DM/(rdrag*z**0.5)
    y3 = z*DH/(rdrag*z**0.5)
    
    dist = {'z': z, 'obs1': y1, 'obs2':y2, 'obs3':y3}
    distances = pd.DataFrame(data=dist)
    
    print('returning the BAO observables \n')
    
    return distances

In [ ]:
LCDM=get_distances(LCDM_params)
my_model=get_distances(my_params)

In [ ]:
fig, ax = plt.subplots(1,1, figsize = (7,5))

ax.set_title('BAO (Models vd Data)')

ax.set_xscale('linear')
ax.set_yscale('linear')

ax.set_xlim(0.1,2.5)
ax.set_ylim(5,28)

ax.set_ylabel(r'Distance/($r_s \sqrt{z}$)')
ax.set_xlabel(r'Redshift')

ax.grid(lw=0.5, ls='--')

#data
ax.errorbar(DV_rs['z'],(DV_rs["quantity"]/DV_rs['z']**0.5), yerr=DV_rs["sigma"]/DV_rs['z']**0.5, alpha=1, color="navy", marker='o', markersize=3, capsize=1, capthick=1,linestyle="none",label=r"$D_V(z)/(r_s \sqrt{z} \,)$")
#model
ax.plot(LCDM['z'],LCDM['obs1'],c='navy')
ax.plot(my_model['z'],my_model['obs1'],ls='--',c='navy')

#data
ax.errorbar(DM_rs['z'],(DM_rs["quantity"]/DM_rs["z"]**0.5) ,yerr=DM_rs["sigma"]/DM_rs["z"]**0.5, alpha=1,color="darkred", marker='o', markersize=3, capsize=1, capthick=1,linestyle="none", label=r"$D_M(z)/(r_s\sqrt{z} \,)$")
#model
ax.plot(LCDM['z'],LCDM['obs2'],c='darkred')
ax.plot(my_model['z'],my_model['obs2'],ls='--',c='darkred')

#data
ax.errorbar(c_Hrs['z'],(c_Hrs['z']*c_Hrs["quantity"])/(c_Hrs["z"]**0.5), yerr=(c_Hrs['z']*c_Hrs["sigma"])/(c_Hrs["z"]**0.5), alpha=1,color="darkgreen",  marker='o', markersize=3,capsize=1, capthick=1,linestyle="none", label=r"$z D_H(z) / (r_s\sqrt{z} \,)$")
#model
ax.plot(LCDM['z'],LCDM['obs3'],c='darkgreen')
ax.plot(my_model['z'],my_model['obs3'],ls='--',c='darkgreen')

#Fake plot for legends
ax.plot(LCDM['z'],100*LCDM['obs2'], c='k', ls='-', label= r'$\Lambda$CDM')
ax.plot(my_model['z'],100*my_model['obs2'], c='k', ls='--', label= r'My Model')

ax.legend(ncol=2)
plt.show()

# Supernovae Distance Moduli Measurements (SN)

In [ ]:
SN=pd.read_csv("../data/Pantheon_plus.txt", sep='\s+')
SN=pd.read_csv("../data/Pantheon_plus.txt", sep='\s+',header=None, skiprows=1, names=SN.keys()[1:len(SN.keys())])
SN=SN.sort_values('z')

In [ ]:
def get_moduli(model,z, mu_b=-19.4):
    
    results=camb.get_results(model)

    DA = results.angular_diameter_distance(z)
    DL = DA*(1 + z)**2
    distance_moduli=5*np.log10(DL)+25+mu_b
    
    return distance_moduli

In [ ]:
LCDM_moduli=get_moduli(LCDM_params,SN['z'])
my_model_moduli=get_moduli(my_params,SN['z'])

In [ ]:
fig, ax = plt.subplots(1,1, figsize = (7,5))

ax.set_title('SN (Models vs Data)')

ax.set_xscale('linear')
ax.set_yscale('linear')

ax.set_xlim(-0.1,2.5)
ax.grid(lw=0.5, ls='--')

ax.set_ylabel(r'Distance Moduli')
ax.set_xlabel(r'Redshift (z)')

ax.plot(SN['z'], LCDM_moduli,ls='-', label=r'ΛCDM',c='DarkRed')
ax.plot(SN['z'], my_model_moduli,ls='-', label=r'my model',c='Darkgreen')
ax.errorbar(SN['z'] ,SN['Moduli'], yerr=SN['Error'], alpha=1,color="k", marker='o', markersize=3, capsize=1, capthick=1,linestyle="none", label=r"Pantheon+")
plt.legend(loc='lower right')
plt.show()